# Chapter 35 - Convolutional Neural Networks
## Building Machine Learning and Deep Learning Models on Google Cloud Platform
### Ekaba Bisong

In [0]:
# import TensorFlow 2.0 with GPU
!pip install -q tf-nightly-gpu-2.0-preview

In [0]:
# import packages
import tensorflow as tf

In [0]:
# confirm tensorflow can see GPU
device_name = tf.test.gpu_device_name()
if device_name != '/device:GPU:0':
  raise SystemError('GPU device not found')
print('Found GPU at: {}'.format(device_name))

Found GPU at: /device:GPU:0


In [0]:
# load the TensorBoard notebook extension
%load_ext tensorboard

In [0]:
# import dataset
(x_train, y_train), (x_test, y_test) = tf.keras.datasets.cifar10.load_data()

In [0]:
# change datatype to float
x_train = x_train.astype('float32')
x_test = x_test.astype('float32')

In [0]:
# scale the dataset from 0 -> 255 to 0 -> 1
x_train /= 255
x_test /= 255

In [0]:
# one-hot encode targets
y_train = tf.keras.utils.to_categorical(y_train)
y_test = tf.keras.utils.to_categorical(y_test)

In [0]:
# parameters
batch_size = 100

In [0]:
# create dataset pipeline
train_ds = tf.data.Dataset.from_tensor_slices(
    (x_train, y_train)).shuffle(len(x_train)).repeat().batch(batch_size)
test_ds = tf.data.Dataset.from_tensor_slices((x_test, y_test)).batch(batch_size)

In [0]:
# create the model
def model_fn():
    model_input = tf.keras.layers.Input(shape=(32, 32, 3))
    x = tf.keras.layers.Conv2D(64, (5, 5), padding='same', activation='relu')(model_input)
    x = tf.keras.layers.Conv2D(64, (5, 5), padding='same', activation='relu')(x)
    x = tf.keras.layers.BatchNormalization()(x)
    x = tf.keras.layers.Conv2D(64, (5, 5), padding='same', activation='relu')(x)
    x = tf.keras.layers.MaxPooling2D(pool_size=(2, 2), strides=2, padding='same')(x)
    x = tf.keras.layers.Conv2D(64, (5, 5), padding='same', activation='relu')(x)
    x = tf.keras.layers.Conv2D(64, (5, 5), padding='same', activation='relu')(x)
    x = tf.keras.layers.BatchNormalization()(x)
    x = tf.keras.layers.MaxPooling2D(pool_size=(2, 2), strides=2, padding='same')(x)
    x = tf.keras.layers.Conv2D(32, (3, 3), padding='same', activation='relu')(x)
    x = tf.keras.layers.Conv2D(32, (3, 3), padding='same', activation='relu')(x)
    x = tf.keras.layers.Conv2D(32, (3, 3), padding='same', activation='relu')(x)
    x = tf.keras.layers.MaxPooling2D(pool_size=(2, 2), strides=2, padding='same')(x)
    x = tf.keras.layers.Dropout(0.3)(x)
    x = tf.keras.layers.Flatten()(x)
    x = tf.keras.layers.Dense(512, activation='relu')(x)
    x = tf.keras.layers.Dense(256, activation='relu')(x)
    x = tf.keras.layers.Dropout(0.5)(x)
    output = tf.keras.layers.Dense(10, activation='softmax')(x)
    
    # the model
    model = tf.keras.Model(inputs=model_input, outputs=output)
    
    # compile the model
    model.compile(optimizer=tf.keras.optimizers.Nadam(),
                  loss='categorical_crossentropy',
                  metrics=['accuracy'])
    return model

In [0]:
# build the model
model = model_fn()

In [0]:
# print model summary
model.summary()

Model: "model"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         [(None, 32, 32, 3)]       0         
_________________________________________________________________
conv2d (Conv2D)              (None, 32, 32, 64)        4864      
_________________________________________________________________
conv2d_1 (Conv2D)            (None, 32, 32, 64)        102464    
_________________________________________________________________
batch_normalization (BatchNo (None, 32, 32, 64)        256       
_________________________________________________________________
conv2d_2 (Conv2D)            (None, 32, 32, 64)        102464    
_________________________________________________________________
max_pooling2d (MaxPooling2D) (None, 16, 16, 64)        0         
_________________________________________________________________
conv2d_3 (Conv2D)            (None, 16, 16, 64)        102464

In [0]:
# tensorboard
tensorboard = tf.keras.callbacks.TensorBoard(log_dir='./tmp/logs_cifar10_keras',
                                             histogram_freq=0, write_graph=True,
                                             write_images=True)

In [0]:
# assign callback
callbacks = [tensorboard]

In [0]:
# train the model
history = model.fit(train_ds, epochs=10,
                    steps_per_epoch=500,
                    callbacks=callbacks)

Epoch 1/10


W0610 00:15:05.157282 139950820616064 deprecation.py:323] From /usr/local/lib/python3.6/dist-packages/tensorflow_core/python/ops/math_grad.py:1251: add_dispatch_support.<locals>.wrapper (from tensorflow.python.ops.array_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where


  1/500 [..............................] - ETA: 1:02:59 - loss: 2.4841 - accuracy: 0.0800

W0610 00:15:12.508325 139950820616064 callbacks.py:241] Method (on_train_batch_end) is slow compared to the batch update (0.262756). Check your callbacks.


500/500 [==============================] - 29s 59ms/step - loss: 1.6574 - accuracy: 0.3895
Epoch 2/10
500/500 [==============================] - 22s 44ms/step - loss: 1.2072 - accuracy: 0.5695
Epoch 3/10
500/500 [==============================] - 21s 43ms/step - loss: 0.9736 - accuracy: 0.6613
Epoch 4/10
500/500 [==============================] - 21s 43ms/step - loss: 0.8398 - accuracy: 0.7096
Epoch 5/10
500/500 [==============================] - 21s 43ms/step - loss: 0.7509 - accuracy: 0.7429
Epoch 6/10
500/500 [==============================] - 22s 43ms/step - loss: 0.6832 - accuracy: 0.7646
Epoch 7/10
500/500 [==============================] - 21s 43ms/step - loss: 0.6271 - accuracy: 0.7859
Epoch 8/10
500/500 [==============================] - 22s 43ms/step - loss: 0.5760 - accuracy: 0.8008
Epoch 9/10
500/500 [==============================] - 22s 43ms/step - loss: 0.5425 - accuracy: 0.8139
Epoch 10/10
500/500 [==============================] - 22s 43ms/step - loss: 0.5032 - accurac

In [0]:
# evaluate the model
score = model.evaluate(test_ds)

100/100 [==============================] - 2s 17ms/step - loss: 0.6716 - accuracy: 0.7754


In [0]:
print('Test loss: {:.2f} \nTest accuracy: {:.2f}%'.format(score[0], score[1]*100))

Test loss: 0.67 
Test accuracy: 77.54%


In [0]:
# execute the command to run TensorBoard
%tensorboard --logdir tmp/logs_cifar10_keras